# TP1 - Aprendizaje Por Refuerzos
## Integrantes:
- **Azul Noguera** 
- **Paula Jordan** 
- **Rocio Gonzalez**
- **Valentina Pancaldi**

## Enunciado

Implementar un agente de aprendizaje por refuerzo y un ambiente en el cual el agente puede entrenarse. Esto incluye definir la noción de estado del ambiente, que puede no coincidir con el estado del juego.

## Preparación del Entorno

In [ ]:
# importamos las clases
from utils import *
from jugador import * # importamos la clase Jugador
from diezmil import * # importamos la clase DiezMil

# importamos funciones de utilidad
from utils import puntaje_y_no_usados, separar, JUGADA_PLANTARSE, JUGADA_TIRAR, JUGADAS_STR

# importamos las librerias necesarias
import numpy as np
from collections import defaultdict
from tqdm import tqdm
import random
from random import randint
import csv

## Estado

In [ ]:
class EstadoDiezMil:
    def __init__(self):
        """Definir qué hace a un estado de diez mil.
        Recordar que la complejidad del estado repercute en la complejidad de la tabla del agente de q-learning.
        """
        self.dados = []  # Lista de los valores actuales de los dados
        self.puntaje_actual = 0  # Puntaje acumulado en el turno actual
        self.turno_terminado = False  # Flag para indicar si el turno ha terminado

    def reset(self):
        """Reinicia el estado del juego a sus valores iniciales."""
        self.dados = self.lanzar_dados(6)  # Reiniciar los dados
        self.puntaje_actual = 0  # Reiniciar el puntaje acumulado
        self.turno_terminado = False  # Reiniciar el flag de turno terminado

    def lanzar_dados(self, cantidad: int) -> list[int]:
        """Simula el lanzamiento de una cantidad específica de dados.
        Args:
            cantidad (int): La cantidad de dados a lanzar.
        Returns:
            list[int]: Los valores obtenidos en los dados lanzados.
        """
        return [randint(1, 6) for _ in range(cantidad)]

    def obtener_estado(self):
        """Devuelve el estado actual del juego en un formato que el agente pueda utilizar."""
        return (self.dados, self.puntaje_actual, self.turno_terminado)

    def actualizar_estado(self, nuevos_dados: list[int], puntaje: int) -> None:
        """Modifica las variables internas del estado luego de una tirada.
        Args:
            nuevos_dados (list[int]): Dados no usados tras la tirada.
            puntaje (int): Puntaje obtenido en la tirada.
        """
    
        self.dados = nuevos_dados
        self.puntaje_actual += puntaje
        if len(self.dados) == 0:
            # Si no quedan dados no usados, el turno debe terminar
            self.turno_terminado = True
    
    def fin_turno(self):
        """Modifica el estado al terminar el turno.
        """
        self.turno_terminado = True  # Marca el turno como terminado

    def __str__(self):
        """Representación en texto de EstadoDiezMil.
        Ayuda a tener una versión legible del objeto.

        Returns:
            str: Representación en texto de EstadoDiezMil.
        """
        estado_str = f"Dados: {self.dados}, Puntaje Actual: {self.puntaje_actual}, Turno Terminado: {self.turno_terminado}"
        return estado_str   

## Ambiente

In [ ]:
class AmbienteDiezMil:
    
    def __init__(self):
        """Definir las variables de instancia de un ambiente.
        ¿Qué es propio de un ambiente de 10.000?
        """
        self.estado = EstadoDiezMil()
        self.turno_terminado = False  # flag que indica si el turno terminó
        self.puntaje_total = 0  # Mantener un registro del puntaje total
        self.pasos_totales = 0  # Contador de pasos
        self.episodios_totales = 0  # Contador de episodios

    def reset(self):
        """
        Reinicia el estado del ambiente.
        """
        if self.pasos_totales > 0:  # Solo sumar episodios si se han realizado pasos
            self.episodios_totales += 1
        self.estado.reset()
        self.turno_terminado = False
        self.pasos_totales = 0
        
        # Aquí no reseteamos `self.puntaje_total` para mantener el acumulado entre episodios.
        return self.estado.obtener_estado()
    
    def step(self, accion):
        """
        Dada una acción devuelve una recompensa.
        El estado es modificado acorde a la acción y su interacción con el ambiente.
        Podría ser útil devolver si terminó o no el turno.
        
        Args:
            accion: Acción elegida por un agente.
        
        Returns:
            tuple[int, bool]: Una recompensa y un flag que indica si terminó el turno. 
        """
        # print(f"\n{'='*50}")
        # print(f"Acción Elegida: {accion.upper()}")

        # print(f"Estado Antes de la Acción: {self.estado}")
        
        self.pasos_totales += 1  # Incrementar el contador de pasos en cada acción
        # print(f"Paso {self.pasos_totales}: Acción = {accion}, Puntaje Total = {self.puntaje_total}")
        
        if accion == 'plantarse':
            self.turno_terminado = True
            recompensa = self.estado.puntaje_actual
            self.puntaje_total += recompensa  # Acumular la recompensa al puntaje total
            
        elif accion == 'tirar':
            nuevos_dados = self.estado.lanzar_dados(len(self.estado.dados))
            puntaje, dados_no_usados = puntaje_y_no_usados(nuevos_dados)
            # print(f"Tirada de Dados: {nuevos_dados}")
            # print(f"Puntaje Calculado: {puntaje}, Dados No Usados: {dados_no_usados}")
            self.estado.actualizar_estado(dados_no_usados, puntaje)
            recompensa = self.estado.puntaje_actual
            self.puntaje_total += recompensa  # Acumular la recompensa al puntaje total
            if recompensa == 0:
                self.turno_terminado = True
        else:
            raise ValueError("Acción no válida.")
        
        # print(f"Estado Después de la Acción: {self.estado}")
        # print(f"Recompensa Obtenida: {recompensa}")
        # print(f"Puntaje Total Acumulado: {self.puntaje_total}")
        # print(f"{'='*50}\n")
        
        return self.estado.obtener_estado(), recompensa, self.turno_terminado

## Agente

In [ ]:
class AgenteQLearning:
    def __init__(self, ambiente: AmbienteDiezMil, alpha: float, gamma: float, epsilon: float):
        self.ambiente = ambiente
        self.alpha = alpha
        self.gamma = gamma
        self.epsilon = epsilon
        self.q_table = {}

    def elegir_accion(self, estado):
        # Convertir cada parte del estado a una tupla si es necesario
        estado = tuple(tuple(part) if isinstance(part, list) else part for part in estado)
        
        if random.uniform(0, 1) < self.epsilon:
            return random.choice(['plantarse', 'tirar'])
        else:
            if estado in self.q_table:
                return max(self.q_table[estado], key=self.q_table[estado].get)
            else:
                return random.choice(['plantarse', 'tirar'])

    def entrenar(self, episodios: int, verbose: bool = False) -> None:
        for episodio in tqdm(range(episodios)):
            estado = self.ambiente.reset()
            estado = tuple(tuple(part) if isinstance(part, list) else part for part in estado)
            terminado = False

            while not terminado:
                accion = self.elegir_accion(estado)
                nuevo_estado, recompensa, terminado = self.ambiente.step(accion)
                nuevo_estado = tuple(tuple(part) if isinstance(part, list) else part for part in nuevo_estado)

                if estado not in self.q_table:
                    self.q_table[estado] = {'plantarse': 0, 'tirar': 0}
                
                if nuevo_estado not in self.q_table:
                    self.q_table[nuevo_estado] = {'plantarse': 0, 'tirar': 0}

                mejor_q_nuevo_estado = max(self.q_table[nuevo_estado].values())
                self.q_table[estado][accion] += self.alpha * (
                    recompensa + self.gamma * mejor_q_nuevo_estado - self.q_table[estado][accion]
                )

                estado = nuevo_estado

                if verbose:
                    print(f"Paso: {episodio + 1}, Estado: {estado}, Acción: {accion}, Recompensa: {recompensa}")

            # # Verificar la condición de finalización del juego
            if self.ambiente.puntaje_total >= 10000:
                print(f"Entrenamiento terminado en el episodio {episodio + 1} con un puntaje total de {self.ambiente.puntaje_total}.")
                break

    def guardar_politica(self, filename: str):
        with open(filename, 'w', newline='') as file:
            writer = csv.writer(file)
            # Guardar encabezado
            writer.writerow(['estado', 'plantarse', 'tirar'])
            for estado, acciones in self.q_table.items():
                # Ordenar los dados dentro del estado antes de convertirlo en cadena
                dados_ordenados = tuple(sorted(estado[0]))  # Suponiendo que los dados son el primer elemento del estado
                estado_ordenado = (dados_ordenados,) + estado[1:]  # Recombina el estado con los dados ordenados
                estado_str = str(estado_ordenado)  # Convertir el estado a una cadena para almacenarlo en el CSV
                writer.writerow([estado_str, acciones['plantarse'], acciones['tirar']])

### Entrenamiento

In [ ]:
class JugadorEntrenado(Jugador):
    def __init__(self, nombre: str, filename_politica: str):
        self.nombre = nombre
        self.politica = self._leer_politica(filename_politica)
        
    def _leer_politica(self, filename:str, SEP:str=','):
        """Carga una politica entrenada con un agente de RL, que está guardada
        en el archivo filename en formato CSV.

        Args:
            filename (str): Nombre/Path del archivo que contiene a una política almacenada. 
        """
        politica = {}
        with open(filename, 'r') as file:
            reader = csv.DictReader(file)
            for row in reader:
                estado = eval(row['estado'])  
                politica[estado] = {
                    'plantarse': float(row['plantarse']),
                    'tirar': float(row['tirar'])
                }
        return politica
    
    def jugar(self, puntaje_total:int, puntaje_turno:int, dados:list[int]) -> tuple[int,list[int]]:
        """
        Devuelve una jugada y los dados a tirar.
        Args:
            puntaje_total (int): Puntaje total del jugador en la partida.
            puntaje_turno (int): Puntaje en el turno del jugador
            dados (list[int]): Tirada del turno.
        Returns:
            tuple[int,list[int]]: Una jugada y la lista de dados a tirar.
        """

        # Calcular el puntaje actual y los dados no usados
        puntaje, no_usados = puntaje_y_no_usados(dados)

        # Definir el estado como una tupla con los componentes relevantes
        estado = (tuple(dados), puntaje_turno, False)  # Matching the structure used in training
        
        # Consultar la política para determinar la jugada
        jugada = self.politica.get(estado, None) 
        if jugada is not None:
            accion = max(jugada, key=jugada.get)  # Choose the action with the highest value
        else:
            print(f"Estado {estado} no encontrado en la política, usando acción por defecto.")
            accion = 'plantarse'  # Default action if the state is not found

        if accion == 'plantarse':
            return ('plantarse', [])
        elif accion == 'tirar':
            return ('tirar', no_usados)

### Ejecución

In [ ]:
ambiente = AmbienteDiezMil()
agente = AgenteQLearning(ambiente, alpha=0.1, gamma=0.9, epsilon=0.2)
agente.entrenar(episodios=100, verbose=True)

### Guardado de Política

In [ ]:
agente.guardar_politica("politica_qlearning.csv")

### Evaluación

In [345]:
jugador = JugadorEntrenado("Agente Trained", "politica_qlearning.csv")
print(jugador.politica)
resultado = jugador.jugar(puntaje_total=0, puntaje_turno=0, dados=[1, 1, 2, 4, 5, 6])

print(resultado)

{((2, 3, 4, 5, 5, 6), 0, False): {'plantarse': 0.0, 'tirar': 0.0}, ((1, 1, 2, 4, 5, 6), 0, False): {'plantarse': 0.0, 'tirar': 15.0}, ((1, 2, 2, 4, 5, 5), 0, False): {'plantarse': 0.0, 'tirar': 10.0}, ((2, 4, 4, 6), 100, False): {'plantarse': 10.0, 'tirar': 0.0}, ((1, 4, 4, 5, 6, 6), 0, False): {'plantarse': 0.0, 'tirar': 0.0}, ((2, 3, 4, 5, 6, 6), 0, False): {'plantarse': 0.0, 'tirar': 150.0}, ((), 1500, True): {'plantarse': 150.0, 'tirar': 0.0}, ((1, 1, 3, 4, 5, 6), 0, False): {'plantarse': 0.0, 'tirar': 0.0}, ((1, 2, 2, 3, 6, 6), 0, False): {'plantarse': 0.0, 'tirar': 0.0}, ((1, 1, 2, 5, 6, 6), 0, False): {'plantarse': 0.0, 'tirar': 10.0}, ((2, 2, 4, 6, 6), 100, False): {'plantarse': 0.0, 'tirar': 20.0}, ((2, 3, 3, 6), 200, False): {'plantarse': 20.0, 'tirar': 0.0}, ((1, 2, 3, 5, 5, 6), 0, False): {'plantarse': 0.0, 'tirar': 20.0}, ((3, 4, 6), 200, False): {'plantarse': 20.0, 'tirar': 0.0}, ((1, 1, 3, 5, 6, 6), 0, False): {'plantarse': 0.0, 'tirar': 15.0}, ((2, 4, 6, 6), 150, False)

### Calculo promedio de varias partidas

Hiperparametros:
- alpha=0.1
- gamma=0.9
- epsilon=0.2

In [394]:
import numpy as np
from tqdm import tqdm

# Definir el número de partidas
numero_partidas = 1000  # Puedes ajustar este número según tus necesidades

# Almacenar los puntajes y el número de pasos de cada partida
puntajes_finales = []
episodios_por_partida = []

for _ in tqdm(range(numero_partidas)):
    # Crear una nueva instancia del ambiente y del agente para cada partida
    ambiente = AmbienteDiezMil()
    agente = AgenteQLearning(ambiente, alpha=0.1, gamma=0.9, epsilon=0.3)
    
    # Entrenar el agente en una partida de 100 episodios
    agente.entrenar(episodios=100, verbose=False)
    
    # Guardar el puntaje final de la partida y el número de pasos
    puntajes_finales.append(ambiente.puntaje_total)
    episodios_por_partida.append(ambiente.episodios_totales)  # Asumiendo que `ambiente.pasos_totales` guarda los pasos realizados

# Guardar la política después de todas las partidas
agente.guardar_politica("politica_qlearning.csv")

# Calcular el promedio de puntajes y el promedio de pasos
promedio_puntajes = np.mean(puntajes_finales)
promedio_pasos = np.mean(episodios_por_partida)

print(f"Promedio de puntajes después de {numero_partidas} partidas: {promedio_puntajes}")
print(f"Promedio de pasos por partida después de {numero_partidas} partidas: {promedio_pasos}")

 30%|███       | 30/100 [00:00<00:00, 23678.80it/s]


Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 200
Paso 1: Acción = plantarse, Puntaje Total = 400
Paso 1: Acción = tirar, Puntaje Total = 400
Paso 2: Acción = plantarse, Puntaje Total = 550
Paso 1: Acción = tirar, Puntaje Total = 700
Paso 2: Acción = tirar, Puntaje Total = 1050
Paso 3: Acción = tirar, Puntaje Total = 1400
Paso 4: Acción = plantarse, Puntaje Total = 1750
Paso 1: Acción = plantarse, Puntaje Total = 2100
Paso 1: Acción = plantarse, Puntaje Total = 2100
Paso 1: Acción = tirar, Puntaje Total = 2100
Paso 2: Acción = tirar, Puntaje Total = 2700
Paso 3: Acción = plantarse, Puntaje Total = 3300
Paso 1: Acción = tirar, Puntaje Total = 3900
Paso 2: Acción = tirar, Puntaje Total = 4150
Paso 3: Acción = tirar, Puntaje Total = 4500
Paso 4: Acción = plantarse, Pun

 20%|██        | 20/100 [00:00<00:00, 22174.49it/s]


Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = tirar, Puntaje Total = 250
Paso 3: Acción = plantarse, Puntaje Total = 600
Paso 1: Acción = tirar, Puntaje Total = 950
Paso 2: Acción = plantarse, Puntaje Total = 1100
Paso 1: Acción = plantarse, Puntaje Total = 1250
Paso 1: Acción = tirar, Puntaje Total = 1250
Paso 2: Acción = plantarse, Puntaje Total = 2000
Paso 1: Acción = plantarse, Puntaje Total = 2750
Paso 1: Acción = plantarse, Puntaje Total = 2750
Paso 1: Acción = plantarse, Puntaje Total = 2750
Paso 1: Acción = tirar, Puntaje Total = 2750
Paso 2: Acción = plantarse, Puntaje Total = 2950
Paso 1: Acción = tirar, Puntaje Total = 3150
Paso 2: Acción = plantarse, Puntaje Total = 3250
Paso 1: Acción = tirar, Puntaje Total = 3350
Paso 2: Acción = plantarse, Puntaje Total = 3600
Paso 1: Acción = plantarse, Puntaje Total = 3850
Paso 1: Acción = tirar, Puntaje Total = 3850
Paso 2: Acción = plantarse, Puntaje Total = 4850
Paso 1: Acci

 15%|█▌        | 15/100 [00:00<00:00, 24798.80it/s]


...

  6%|▌         | 6/100 [00:00<00:00, 5843.01it/s]


Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 500
Paso 1: Acción = tirar, Puntaje Total = 1000
Paso 2: Acción = plantarse, Puntaje Total = 1050
Paso 1: Acción = tirar, Puntaje Total = 1100
Paso 2: Acción = tirar, Puntaje Total = 2150
Paso 3: Acción = tirar, Puntaje Total = 3200
Paso 4: Acción = plantarse, Puntaje Total = 4250
Paso 1: Acción = tirar, Puntaje Total = 5300
Paso 2: Acción = plantarse, Puntaje Total = 5450
Paso 1: Acción = plantarse, Puntaje Total = 5600
Paso 1: Acción = tirar, Puntaje Total = 5600
Paso 2: Acción = plantarse, Puntaje Total = 5650
Paso 1: Acción = tirar, Puntaje Total = 5700
Paso 2: Acción = plantarse, Puntaje Total = 8700
Entrenamiento terminado en el episodio 7 con un puntaje total de 11700.


100%|██████████| 1000/1000 [00:07<00:00, 130.24it/s]

Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 300
Paso 1: Acción = tirar, Puntaje Total = 600
Paso 2: Acción = plantarse, Puntaje Total = 1200
Paso 1: Acción = plantarse, Puntaje Total = 1800
Paso 1: Acción = tirar, Puntaje Total = 1800
Paso 2: Acción = plantarse, Puntaje Total = 2850
Paso 1: Acción = tirar, Puntaje Total = 3900
Paso 2: Acción = tirar, Puntaje Total = 4450
Paso 3: Acción = plantarse, Puntaje Total = 5050
Paso 1: Acción = tirar, Puntaje Total = 5650
Paso 2: Acción = plantarse, Puntaje Total = 5750
Paso 1: Acción = plantarse, Puntaje Total = 5850
Paso 1: Acción = tirar, Puntaje Total = 5850
Paso 2: Acción = tirar, Puntaje Total = 6050
Paso 3: Acción = plantarse, Puntaje Total = 6350
Paso 1: Acción = plantarse, Puntaje Total = 6650
Paso 1: Acción = plantarse, Puntaje Total = 6650
Paso 1: Acción = tirar, Puntaje Total = 6650
Paso 2: Acción = plantarse, Puntaje Total = 6800
Paso 1: Acción 

Promedio de puntajes después de 1000 partidas: 12547.75
Promedio de pasos por partida después de 1000 partidas: 22.143


In [395]:
print(f"Promedio de puntajes después de {numero_partidas} partidas: {promedio_puntajes}")
print(f"Promedio de pasos por partida después de {numero_partidas} partidas: {promedio_pasos}")

Promedio de puntajes después de 1000 partidas: 12547.75
Promedio de pasos por partida después de 1000 partidas: 22.143


In [396]:
print(puntajes_finales)
print(episodios_por_partida)

[10200, 11250, 10400, 10400, 14750, 10500, 10450, 11700, 11250, 15100, 12600, 11050, 12000, 11250, 10600, 11700, 11700, 10550, 10000, 10200, 10800, 14800, 12200, 10100, 10450, 10550, 11000, 12550, 25500, 11800, 10300, 10250, 10000, 13450, 11950, 11300, 11350, 10150, 10300, 10000, 10600, 27650, 10950, 10800, 10100, 12350, 10000, 10150, 16500, 10800, 11850, 12000, 10000, 10900, 19900, 10850, 10050, 10000, 10800, 12000, 10050, 11000, 10750, 10950, 10650, 10200, 12800, 11900, 12650, 10250, 10450, 10750, 11050, 10100, 64300, 23000, 10100, 10750, 10050, 10400, 10100, 37100, 10500, 10250, 10350, 18450, 10000, 10050, 11900, 13100, 10450, 10600, 11200, 10600, 11600, 10150, 12100, 10700, 22500, 11500, 10400, 10400, 10850, 10050, 10200, 10300, 10300, 11400, 11700, 10950, 10550, 10250, 10800, 11150, 10100, 38850, 10150, 11100, 10100, 10550, 12100, 11300, 10350, 10300, 10950, 10250, 11550, 10350, 14700, 10150, 10800, 17600, 12400, 12750, 10250, 10550, 10950, 11600, 10100, 10500, 10450, 11250, 10050

## Nuevo Agente

- Decaimiento del Epsilon: En lugar de utilizar un valor fijo de epsilon para la exploración, puedes implementar un epsilon decay que reduzca gradualmente la tasa de exploración a medida que el agente aprende más. Esto permite que el agente explore al principio y, eventualmente, explote el conocimiento adquirido.

In [401]:
class AgenteQLearning2:
    def __init__(self, ambiente: AmbienteDiezMil, alpha: float, gamma: float, epsilon: float, epsilon_decay: float = 0.995):
        self.ambiente = ambiente
        self.alpha = alpha
        self.gamma = gamma
        self.epsilon = epsilon
        self.epsilon_decay = epsilon_decay
        self.q_table = {}

    def elegir_accion(self, estado):
        estado = tuple(tuple(part) if isinstance(part, list) else part for part in estado)
        
        if random.uniform(0, 1) < self.epsilon:
            return random.choice(['plantarse', 'tirar'])
        else:
            if estado in self.q_table:
                return max(self.q_table[estado], key=self.q_table[estado].get)
            else:
                return random.choice(['plantarse', 'tirar'])

    def entrenar(self, episodios: int, verbose: bool = False) -> None:
        for episodio in tqdm(range(episodios)):
            estado = self.ambiente.reset()  # Resetea el ambiente para iniciar un nuevo episodio
            estado = tuple(tuple(part) if isinstance(part, list) else part for part in estado)
            terminado = False

            while not terminado:
                accion = self.elegir_accion(estado)
                nuevo_estado, recompensa, terminado = self.ambiente.step(accion)
                nuevo_estado = tuple(tuple(part) if isinstance(part, list) else part for part in nuevo_estado)

                if estado not in self.q_table:
                    self.q_table[estado] = {'plantarse': 0, 'tirar': 0}
                
                if nuevo_estado not in self.q_table:
                    self.q_table[nuevo_estado] = {'plantarse': 0, 'tirar': 0}

                mejor_q_nuevo_estado = max(self.q_table[nuevo_estado].values())
                self.q_table[estado][accion] += self.alpha * (
                    recompensa + self.gamma * mejor_q_nuevo_estado - self.q_table[estado][accion]
                )

                estado = nuevo_estado

                if verbose:
                    print(f"Paso: {episodio + 1}, Estado: {estado}, Acción: {accion}, Recompensa: {recompensa}")

            # Reducir epsilon después de cada episodio
            self.epsilon *= self.epsilon_decay

            if self.ambiente.puntaje_total >= 10000:
                print(f"Entrenamiento terminado en el episodio {episodio + 1} con un puntaje total de {self.ambiente.puntaje_total}.")
                break
    
    def guardar_politica(self, filename: str):
        with open(filename, 'w', newline='') as file:
            writer = csv.writer(file)
            # Guardar encabezado
            writer.writerow(['estado', 'plantarse', 'tirar'])
            for estado, acciones in self.q_table.items():
                # Ordenar los dados dentro del estado antes de convertirlo en cadena
                dados_ordenados = tuple(sorted(estado[0]))  # Suponiendo que los dados son el primer elemento del estado
                estado_ordenado = (dados_ordenados,) + estado[1:]  # Recombina el estado con los dados ordenados
                estado_str = str(estado_ordenado)  # Convertir el estado a una cadena para almacenarlo en el CSV
                writer.writerow([estado_str, acciones['plantarse'], acciones['tirar']])

### Entrenamiento

In [402]:
import numpy as np
from tqdm import tqdm

# Definir el número de partidas
numero_partidas = 1000  # Puedes ajustar este número según tus necesidades

# Parámetros de Q-learning
alpha = 0.2 # Aumenta la tasa de aprendizaje para adaptarse más rápido
gamma = 0.9 # Mantén un enfoque balanceado entre recompensas a corto y largo plazo
epsilon_inicial = 0.8 # Comienza explorando, pero no de forma tan aleatoria como antes
epsilon_minimo = 0.15 # Permite una explotación mayor hacia el final
epsilon_decay = 0.997  # Factor de decaimiento

# Almacenar los puntajes y el número de episodios de cada partida
puntajes_finales = []
episodios_por_partida = []

# Iterar sobre cada partida
for _ in tqdm(range(numero_partidas)):
    # Crear una nueva instancia del ambiente
    ambiente = AmbienteDiezMil()
    
    # Ajustar el epsilon para cada partida
    epsilon_actual = max(epsilon_minimo, epsilon_inicial * (epsilon_decay ** _))
    
    # Crear una nueva instancia del agente para cada partida con el epsilon actual
    agente = AgenteQLearning2(ambiente, alpha=alpha, gamma=gamma, epsilon=epsilon_actual)
    
    # Entrenar el agente en una partida de 100 episodios
    agente.entrenar(episodios=100, verbose=False)
    
    # Guardar el puntaje final de la partida y el número de episodios
    puntajes_finales.append(ambiente.puntaje_total)
    episodios_por_partida.append(ambiente.episodios_totales)  # Asumiendo que `ambiente.episodios_totales` guarda los episodios realizados

# Guardar la política después de todas las partidas
agente.guardar_politica("politica_qlearning.csv")

# Calcular el promedio de puntajes y el promedio de episodios
promedio_puntajes = np.mean(puntajes_finales)
promedio_episodios = np.mean(episodios_por_partida)

print(f"Promedio de puntajes después de {numero_partidas} partidas: {promedio_puntajes}")
print(f"Promedio de episodios por partida después de {numero_partidas} partidas: {promedio_episodios}")

 25%|██▌       | 25/100 [00:00<00:00, 18578.60it/s]


Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = tirar, Puntaje Total = 600
Paso 3: Acción = plantarse, Puntaje Total = 1300
Paso 1: Acción = plantarse, Puntaje Total = 2000
Paso 1: Acción = plantarse, Puntaje Total = 2000
Paso 1: Acción = plantarse, Puntaje Total = 2000
Paso 1: Acción = tirar, Puntaje Total = 2000
Paso 2: Acción = plantarse, Puntaje Total = 2400
Paso 1: Acción = tirar, Puntaje Total = 2800
Paso 2: Acción = plantarse, Puntaje Total = 3050
Paso 1: Acción = plantarse, Puntaje Total = 3300
Paso 1: Acción = plantarse, Puntaje Total = 3300
Paso 1: Acción = tirar, Puntaje Total = 3300
Paso 2: Acción = plantarse, Puntaje Total = 3450
Paso 1: Acción = tirar, Puntaje Total = 3600
Paso 2: Acción = plantarse, Puntaje Total = 4250
Paso 1: Acción = plantarse, Puntaje Total = 4900
Paso 1: Acción = plantarse, Puntaje Total = 4900
Paso 1: Acción = tirar, Puntaje Total = 4900
Paso 2: Acción = plantarse, Puntaje Total = 5000
Paso 1

 11%|█         | 11/100 [00:00<00:00, 22919.69it/s]


Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 300
Paso 1: Acción = tirar, Puntaje Total = 600
Paso 2: Acción = plantarse, Puntaje Total = 750
Paso 1: Acción = tirar, Puntaje Total = 900
Paso 2: Acción = tirar, Puntaje Total = 1050
Paso 3: Acción = plantarse, Puntaje Total = 1400
Paso 1: Acción = tirar, Puntaje Total = 1750
Paso 2: Acción = plantarse, Puntaje Total = 2250
Paso 1: Acción = plantarse, Puntaje Total = 2750
Paso 1: Acción = tirar, Puntaje Total = 2750
Paso 2: Acción = plantarse, Puntaje Total = 2850
Paso 1: Acción = tirar, Puntaje Total = 2950
Paso 2: Acción = plantarse, Puntaje Total = 3200
Paso 1: Acción = plantarse, Puntaje Total = 3450
Paso 1: Acción = plantarse, Puntaje Total = 3450
Paso 1: Acción = plantarse, Puntaje Total = 3450
Paso 1: Acción = tirar, Puntaje Total = 3450
Paso 2: Acción = tirar, Puntaje Total = 6450
Paso 3: Acción = tirar, Puntaje Total = 9450
Paso 4: Acción = tira

 30%|███       | 30/100 [00:00<00:00, 36272.45it/s]


...

Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = plantarse, Puntaje Total = 0
Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 300
Paso 1: Acción = tirar, Puntaje Total = 600
Paso 2: Acción = plantarse, Puntaje Total = 1650
Paso 1: Acción = plantarse, Puntaje Total = 2700
Paso 1: Acción = tirar, Puntaje Total = 2700
Paso 2: Acción = tirar, Puntaje Total = 2800
Paso 3: Acción = plantarse, Puntaje Total = 3050
Paso 1: Acción = tirar, Puntaje Total = 3300
Paso 2: Acción = plantarse, Puntaje Total = 3550
Paso 1: Acción = tirar, Puntaje Total = 3800
Paso 2: Acción = plantarse, Puntaje Total = 4050
Paso 1: Acción = plantarse, Puntaje Total = 4300
Paso 1: Acción = tirar, Puntaje Total = 4300
Paso 2: Acción = plantarse, Puntaje Total = 4500
Paso 1: Acción = tirar, Puntaje Total = 4700
Paso 2: Acción = plantarse, Puntaje Total = 5400
Paso 1: Acción = tirar, Puntaje Total = 6100
Paso 2: Acción = plantarse, Puntaje Total = 6350
Paso 1: Acción = t


 24%|██▍       | 24/100 [00:00<00:00, 8774.69it/s]


Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 100
Paso 1: Acción = plantarse, Puntaje Total = 200
Paso 1: Acción = plantarse, Puntaje Total = 200
Paso 1: Acción = tirar, Puntaje Total = 200
Paso 2: Acción = plantarse, Puntaje Total = 400
Paso 1: Acción = tirar, Puntaje Total = 600
Paso 2: Acción = plantarse, Puntaje Total = 850
Paso 1: Acción = plantarse, Puntaje Total = 1100
Paso 1: Acción = plantarse, Puntaje Total = 1100
Paso 1: Acción = tirar, Puntaje Total = 1100
Paso 2: Acción = plantarse, Puntaje Total = 1350
Paso 1: Acción = tirar, Puntaje Total = 1600
Paso 2: Acción = plantarse, Puntaje Total = 1850
Paso 1: Acción = plantarse, Puntaje Total = 2100
Paso 1: Acción = tirar, Puntaje Total = 2100
Paso 2: Acción = plantarse, Puntaje Total = 2200
Paso 1: Acción = plantarse, Puntaje Total = 2300
Paso 1: Acción = plantarse, Puntaje Total = 2300
Paso 1: Acción = plantarse, Puntaje Total = 2300
Paso 1: Acción = tirar, Puntaje Total = 2300
Paso 2: A

100%|██████████| 1000/1000 [00:07<00:00, 131.24it/s]


Paso 1: Acción = tirar, Puntaje Total = 0
Paso 2: Acción = plantarse, Puntaje Total = 300
Paso 1: Acción = plantarse, Puntaje Total = 600
Paso 1: Acción = plantarse, Puntaje Total = 600
Paso 1: Acción = tirar, Puntaje Total = 600
Paso 2: Acción = plantarse, Puntaje Total = 850
Paso 1: Acción = plantarse, Puntaje Total = 1100
Paso 1: Acción = tirar, Puntaje Total = 1100
Paso 2: Acción = plantarse, Puntaje Total = 1400
Paso 1: Acción = plantarse, Puntaje Total = 1700
Paso 1: Acción = tirar, Puntaje Total = 1700
Paso 2: Acción = plantarse, Puntaje Total = 2300
Paso 1: Acción = plantarse, Puntaje Total = 2900
Paso 1: Acción = plantarse, Puntaje Total = 2900
Paso 1: Acción = tirar, Puntaje Total = 2900
Paso 2: Acción = plantarse, Puntaje Total = 3500
Paso 1: Acción = tirar, Puntaje Total = 4100
Paso 2: Acción = plantarse, Puntaje Total = 7100
Entrenamiento terminado en el episodio 12 con un puntaje total de 10100.
Promedio de puntajes después de 1000 partidas: 12017.3
Promedio de episodios 

In [405]:
print(f"Promedio de puntajes después de {numero_partidas} partidas: {promedio_puntajes}")
print(f"Promedio de pasos por partida después de {numero_partidas} partidas: {promedio_episodios}")

Promedio de puntajes después de 1000 partidas: 12017.3
Promedio de pasos por partida después de 1000 partidas: 22.493


In [406]:
print(episodios_por_partida)

[25, 11, 30, 9, 11, 7, 17, 21, 13, 20, 16, 17, 8, 13, 7, 20, 6, 11, 32, 20, 27, 25, 14, 24, 16, 10, 20, 7, 16, 29, 9, 17, 18, 6, 16, 13, 8, 19, 25, 22, 17, 21, 2, 14, 12, 18, 25, 24, 10, 19, 20, 25, 15, 23, 14, 17, 20, 26, 44, 12, 15, 22, 28, 27, 22, 34, 0, 7, 18, 15, 25, 29, 21, 18, 19, 24, 14, 18, 14, 14, 25, 37, 8, 1, 17, 26, 14, 23, 24, 15, 18, 18, 12, 14, 33, 13, 40, 18, 17, 30, 21, 23, 8, 11, 5, 28, 14, 21, 42, 19, 24, 31, 32, 14, 38, 29, 4, 20, 23, 10, 20, 22, 22, 18, 14, 19, 18, 44, 15, 34, 28, 11, 19, 15, 25, 29, 23, 27, 22, 29, 30, 15, 19, 22, 18, 41, 15, 16, 10, 33, 17, 14, 18, 10, 11, 22, 34, 17, 22, 36, 20, 24, 11, 26, 20, 21, 28, 7, 18, 26, 13, 22, 24, 11, 9, 12, 27, 14, 14, 7, 20, 4, 21, 14, 18, 21, 24, 11, 21, 4, 22, 15, 37, 17, 3, 18, 22, 10, 40, 20, 15, 25, 18, 34, 33, 13, 14, 20, 27, 11, 22, 16, 16, 22, 27, 11, 24, 21, 24, 31, 30, 19, 15, 20, 18, 15, 10, 43, 18, 6, 27, 34, 24, 32, 21, 28, 20, 17, 31, 21, 16, 30, 15, 16, 14, 28, 26, 7, 27, 20, 11, 17, 25, 24, 40, 24, 